In [1]:
import pandas as pd
import numpy as np
pd.set_option('display.max_columns', 100)
import ast

import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px

from sklearn.feature_extraction.text import CountVectorizer
from nltk.corpus import stopwords
english_stops = stopwords.words("english")

# from google.colab import files
# import io

In [2]:
import plotly
plotly.__version__

'5.3.1'

# Sources
- EDA tutorial : https://www.youtube.com/watch?v=u64sWJEP4S0
- 2015 data source : https://data.seattle.gov/dataset/2015-Building-Energy-Benchmarking/h7rm-fz6m
- 2016 data source : https://data.seattle.gov/dataset/2016-Building-Energy-Benchmarking/2bpz-gwpy

# Importation des données

In [3]:
# uploaded = files.upload()
# data_2015 = pd.read_csv(io.BytesIO(uploaded["2015-building-energy-benchmarking.csv"]))
# data_2016 = pd.read_csv(io.BytesIO(uploaded["2016-building-energy-benchmarking.csv"]))

In [4]:
data_2015 = pd.read_csv("datasets/2015-building-energy-benchmarking.csv")
data_2016 = pd.read_csv("datasets/2016-building-energy-benchmarking.csv")

# Dictionnaire des données

Voici une définition de chacune des variables de notre jeu de données (source : data.seattle.gov).

| Column Name | Description |
| --- | --- |
| OSEBuildingID | A unique identifier assigned to each property covered by the Seattle Benchmarking Ordinance for tracking and identification purposes. |
| DataYear | |
| BuildingType | City of Seattle building type classification. |
|PrimaryPropertyType| The primary use of a property (e.g. office, retail store). Primary use is defined as a function that accounts for more than 50% of a property. This is the Property Type - EPA Calculated field from Portfolio Manager. |
| PropertyName | Official or common property name.|
|TaxParcellIdentificationNumber| Property King County PIN|
|Location| |
|CouncilDistrictCode | Property City of Seattle council district.|
|Neighborhood | Property neighborhood area defined by the City of Seattle Department of Neighborhoods. |
|YearBuilt| Year in which a property was constructed or underwent a complete renovation.|
NumberofBuildings| Number of buildings included in the property's report. In cases where a property is reporting as a campus, multiple buildings may be included in one report. |
NumberofFloors| Number of floors reported in Portfolio Manager |
PropertyGFATotal | Total building and parking gross floor area.|
PropertyGFAParking| Total space in square feet of all types of parking (Fully Enclosed, Partially Enclosed, and Open). |
PropertyGFABuilding(s)| Total floor space in square feet between the outside surfaces of a building’s enclosing walls. This includes all areas inside the building(s), such as tenant space, common areas, stairwells, basements, storage, etc. |
ListOfAllPropertyUseTypes| All property uses reported in Portfolio Manager |
LargestPropertyUseType|The largest use of a property (e.g. office, retail store) by GFA.|
LargestPropertyUseTypeGFA| The gross floor area (GFA) of the largest use of the property. |
ENERGYSTARScore| An EPA calculated 1-100 rating that assesses a property’s overall energy performance, based on national data to control for differences among climate, building uses, and operations. A score of 50 represents the national median. |
SiteEUI(kBtu/sf)| Site Energy Use Intensity (EUI) is a property's Site Energy Use divided by its gross floor area. Site Energy Use is the annual amount of all the energy consumed by the property on-site, as reported on utility bills. Site EUI is measured in thousands of British thermal units (kBtu) per square foot. |
SiteEUIWN(kBtu/sf)| Weather Normalized (WN) Site Energy Use Intensity (EUI) is a property's WN Site Energy divided by its gross floor area (in square feet). WN Site Energy is the Site Energy Use the property would have consumed during 30-year average weather conditions. WN Site EUI is measured in measured in thousands of British thermal units (kBtu) per square foot. |
SourceEUI(kBtu/sf)| Source Energy Use Intensity (EUI) is a property's Source Energy Use divided by its gross floor area. Source Energy Use is the annual energy used to operate the property, including losses from generation, transmission, & distribution. Source EUI is measured in thousands of British thermal units (kBtu) per square foot. |
SourceEUIWN(kBtu/sf)| Weather Normalized (WN) Source Energy Use Intensity (EUI) is a property's WN Source Energy divided by its gross floor area. WN Source Energy is the Source Energy Use the property would have consumed during 30-year average weather conditions. WN Source EUI is measured in measured in thousands of British thermal units (kBtu) per square foot. |
SiteEnergyUse(kBtu)| The annual amount of energy consumed by the property from all sources of energy. |
SiteEnergyUseWN(kBtu)| The annual amount of energy consumed by the property from all sources of energy, adjusted to what the property would have consumed during 30-year average weather conditions.|
SteamUse(kBtu)| The annual amount of district steam consumed by the property on-site, measured in thousands of British thermal units (kBtu). |
Electricity(kWh)| The annual amount of electricity consumed by the property on-site, including electricity purchased from the grid and generated by onsite renewable systems, measured in kWh |
Electricity(kBtu)| The annual amount of electricity consumed by the property on-site, including electricity purchased from the grid and generated by onsite renewable systems, measured in thousands of British thermal units (kBtu). |
NaturalGas(therms)| The annual amount of utility-supplied natural gas consumed by the property, measured in therms. |
NaturalGas(kBtu)| The annual amount of utility-supplied natural gas consumed by the property, measured in thousands of British thermal units (kBtu).|
OtherFuelUse(kBtu)||
GHGEmissions(MetricTonsCO2e)| The total amount of greenhouse gas emissions, including carbon dioxide, methane, and nitrous oxide gases released into the atmosphere as a result of energy consumption at the property, measured in metric tons of carbon dioxide equivalent. This calculation uses a GHG emissions factor from Seattle CIty Light's portfolio of generating resources. This uses Seattle City Light's 2015 emissions factor of 52.44 lbs CO2e/MWh. Enwave steam factor = 170.17 lbs CO2e/MMBtu. Gas factor sourced from EPA Portfolio Manager = 53.11 kg CO2e/MBtu. |
GHGEmissionsIntensity(kgCO2e/ft2)| Total Greenhouse Gas Emissions divided by property's gross floor area, measured in kilograms of carbon dioxide equivalent per square foot. This calculation uses a GHG emissions factor from Seattle City Light's portfolio of generating resources |
DefaultData| The property used default data for at least one property characteristic. |
ComplianceStatus| Whether a property has met energy benchmarking requirements for the current reporting year. |
Seattle Police Department Micro Community Policing Plan Areas||
SPD Beats||
Zip Codes| Property zip |

# Fonctions utiles

In [5]:
def get_dataset_name(obj, namespace):
    """ fonction permettant d'afficher le nom d'un jeu de données dans un print."""
    return [name for name in namespace if namespace[name] is obj][0]

def get_dataset_shape(d):
    return print(f">>> {get_dataset_name(d, globals())} contient {d.shape[0]} lignes et {d.shape[1]} colonnes.\n")
    
def get_dataset_duplicates(d):
    return print(f">>> {get_dataset_name(d, globals())} contient {len(d)-len(d.drop_duplicates())} doublon(s).\n")

def get_missing_values_table(d) :
        mis_val = d.isnull().sum()
        mis_val_percent = 100 * d.isnull().sum() / len(d)
        mis_val_table = pd.concat([mis_val, mis_val_percent], axis=1)
        mis_val_table_ren_columns = mis_val_table.rename(
        columns = {0 : 'Missing Values', 1 : '% of Total Values'})
        mis_val_table_ren_columns = mis_val_table_ren_columns[
            mis_val_table_ren_columns.iloc[:,1] != 0].sort_values('% of Total Values', ascending = False).round(2)
        print (f">>> {get_dataset_name(d, globals())} contient {mis_val_table_ren_columns.shape[0]} colonnes avec des valeurs manquantes.")
        return mis_val_table_ren_columns.T
    
def get_features_list(d):
    return print(f">>> {get_dataset_name(d, globals())} contient les variables suivantes :\n {list(d.columns)}\n")

def get_dataset_sample(d):
    np.random.seed(42)
    return d.sample(3)

def get_dataset_overview(d):
    print(f"#################### \033[1m {get_dataset_name(d, globals()).upper()} \033[0m ####################\n")
    get_dataset_shape(d)
    get_features_list(d)
    get_dataset_duplicates(d)
#     get_dataset_features_types(d)
    display(get_missing_values_table(d))
    display(get_dataset_sample(d))

# Nettoyage des données 

## 2015

In [6]:
df_2015 = data_2015.copy()

In [7]:
get_dataset_overview(df_2015)

####################  DF_2015  ####################

>>> df_2015 contient 3340 lignes et 47 colonnes.

>>> df_2015 contient les variables suivantes :
 ['OSEBuildingID', 'DataYear', 'BuildingType', 'PrimaryPropertyType', 'PropertyName', 'TaxParcelIdentificationNumber', 'Location', 'CouncilDistrictCode', 'Neighborhood', 'YearBuilt', 'NumberofBuildings', 'NumberofFloors', 'PropertyGFATotal', 'PropertyGFAParking', 'PropertyGFABuilding(s)', 'ListOfAllPropertyUseTypes', 'LargestPropertyUseType', 'LargestPropertyUseTypeGFA', 'SecondLargestPropertyUseType', 'SecondLargestPropertyUseTypeGFA', 'ThirdLargestPropertyUseType', 'ThirdLargestPropertyUseTypeGFA', 'YearsENERGYSTARCertified', 'ENERGYSTARScore', 'SiteEUI(kBtu/sf)', 'SiteEUIWN(kBtu/sf)', 'SourceEUI(kBtu/sf)', 'SourceEUIWN(kBtu/sf)', 'SiteEnergyUse(kBtu)', 'SiteEnergyUseWN(kBtu)', 'SteamUse(kBtu)', 'Electricity(kWh)', 'Electricity(kBtu)', 'NaturalGas(therms)', 'NaturalGas(kBtu)', 'OtherFuelUse(kBtu)', 'GHGEmissions(MetricTonsCO2e)', 'GHGEm

Comment  Outlier  YearsENERGYSTARCertified  \
Missing Values     3327.00  3256.00                   3230.00   
% of Total Values    99.61    97.49                     96.71   

                   City Council Districts  2010 Census Tracts  \
Missing Values                    3127.00             3116.00   
% of Total Values                   93.62               93.29   

                   ThirdLargestPropertyUseType  \
Missing Values                         2780.00   
% of Total Values                        83.23   

                   ThirdLargestPropertyUseTypeGFA  \
Missing Values                            2780.00   
% of Total Values                           83.23   

                   SecondLargestPropertyUseType  \
Missing Values                          1781.00   
% of Total Values                         53.32   

                   SecondLargestPropertyUseTypeGFA  ENERGYSTARScore  \
Missing Values                             1781.00           780.00   
% of Total Values                            53.32            23.35   

                   LargestPropertyUseTypeGFA  LargestPropertyUseType  \
Missing Values                        136.00                  136.00   
% of Total Values                       4.07                    4.07   

                   ListOfAllPropertyUseTypes  Electricity(kBtu)  \
Missing Values                         127.0               10.0   
% of Total Values                        3.8                0.3   

                   GHGEmissionsIntensity(kgCO2e/ft2)  \
Missing Values                                  10.0   
% of Total Values                                0.3   

                   GHGEmissions(MetricTonsCO2e)  OtherFuelUse(kBtu)  \
Missing Values                             10.0                10.0   
% of Total Values                           0.3                 0.3   

                   NaturalGas(kBtu)  NaturalGas(therms)  \
Missing Values                 10.0                10.0   
% of Total Values               0.3                 0.3   

                   SiteEnergyUseWN(kBtu)  Electricity(kWh)  SteamUse(kBtu)  \
Missing Values                      10.0              10.0            10.0   
% of Total Values                    0.3               0.3             0.3   

                   SiteEnergyUse(kBtu)  SourceEUI(kBtu/sf)  \
Missing Values                    10.0                10.0   
% of Total Values                  0.3                 0.3   

                   SiteEUIWN(kBtu/sf)  SiteEUI(kBtu/sf)  SourceEUIWN(kBtu/sf)  \
Missing Values                   10.0              10.0                  10.0   
% of Total Values                 0.3               0.3                   0.3   

                   NumberofFloors  \
Missing Values               8.00   
% of Total Values            0.24   

                   Seattle Police Department Micro Community Policing Plan Areas  \
Missing Values                                                  2.00               
% of Total Values                                               0.06               

                   TaxParcelIdentificationNumber  SPD Beats  DefaultData  
Missing Values                              2.00       2.00         1.00  
% of Total Values                           0.06       0.06         0.03

OSEBuildingID  DataYear          BuildingType   PrimaryPropertyType  \
479             640      2015        NonResidential          Large Office   
2077          24270      2015        NonResidential      Worship Facility   
705           19662      2015  Multifamily MR (5-9)  Mid-Rise Multifamily   

                       PropertyName TaxParcelIdentificationNumber  \
479         STARBUCKS (SODO) CENTER                    7666207220   
2077  PHINNEY RIDGE LUTHERAN CHURCH                    3362900895   
705                 EL CAPITAN APTS                     660002545   

                                               Location  CouncilDistrictCode  \
479   {'latitude': '47.58133381', 'longitude': '-122...                    2   
2077  {'latitude': '47.68358093', 'longitude': '-122...                    6   
705   {'latitude': '47.61565792', 'longitude': '-122...                    3   

          Neighborhood  YearBuilt  NumberofBuildings  NumberofFloors  \
479   GREATER DUWAMISH       1912                  1             6.0   
2077         NORTHWEST       1951                  1             2.0   
705               EAST       1925                  1             5.0   

      PropertyGFATotal  PropertyGFAParking  PropertyGFABuilding(s)  \
479            1380959                   0                 1380959   
2077             41600                   0                   41600   
705              58954                   0                   58954   

                             ListOfAllPropertyUseTypes LargestPropertyUseType  \
479   Non-Refrigerated Warehouse, Office, Retail Store                 Office   
2077                                  Worship Facility       Worship Facility   
705                                Multifamily Housing    Multifamily Housing   

      LargestPropertyUseTypeGFA SecondLargestPropertyUseType  \
479                   1000730.0                 Retail Store   
2077                    41600.0                          NaN   
705                     58954.0                          NaN   

      SecondLargestPropertyUseTypeGFA ThirdLargestPropertyUseType  \
479                          281296.0  Non-Refrigerated Warehouse   
2077                              NaN                         NaN   
705                               NaN                         NaN   

      ThirdLargestPropertyUseTypeGFA YearsENERGYSTARCertified  \
479                         220303.0                      NaN   
2077                             NaN                      NaN   
705                              NaN                      NaN   

      ENERGYSTARScore  SiteEUI(kBtu/sf)  SiteEUIWN(kBtu/sf)  \
479              77.0              52.1                53.7   
2077             60.0              28.6                35.6   
705              88.0              43.9                52.5   

      SourceEUI(kBtu/sf)  SourceEUIWN(kBtu/sf)  SiteEnergyUse(kBtu)  \
479                151.3                 153.0           78272488.0   
2077                64.1                  75.8            1189432.0   
705                 70.9                  81.0            2585187.0   

      SiteEnergyUseWN(kBtu)  SteamUse(kBtu)  Electricity(kWh)  \
479              80627768.0             0.0        20352100.0   
2077              1481282.0             0.0          198536.0   
705               3096245.0             0.0          205105.0   

      Electricity(kBtu)  NaturalGas(therms)  NaturalGas(kBtu)  \
479          69444248.0             88311.0         8831128.0   
2077           677434.0              5120.0          512026.0   
705            699846.0             18854.0         1885370.0   

      OtherFuelUse(kBtu)  GHGEmissions(MetricTonsCO2e)  \
479                  0.0                        953.12   
2077                 0.0                         31.92   
705                  0.0                        105.01   

      GHGEmissionsIntensity(kgCO2e/ft2) DefaultData Comment ComplianceStatus  \
479                                0

Supprimons les variables avec __plus de 50%__ de valeurs manquantes :

In [8]:
df_2015 = df_2015.loc[:, df_2015.isnull().mean() < .5]

Examinons la variable `Location` : 

In [9]:
df_2015["Location"].head(3)

0    {'latitude': '47.61219025', 'longitude': '-122...
1    {'latitude': '47.61310583', 'longitude': '-122...
2    {'latitude': '47.61334897', 'longitude': '-122...
Name: Location, dtype: object

Cette variable semblent contenir des dictionnaires contenant des __informations sur la localisation du bâtiment__ (latitude, longitude, addresse, ville, état, et code postal). Nous allons créer, pour chaque champ du dictionnaire, une nouvelle variable dans `df_2015`. La fonction `extract_location_features()` récupère les informations du dictionnaire et les stocke dans des variables.

In [10]:
def extract_location_features(my_string):
    result = ast.literal_eval(my_string)  # transformation de la chaîne de charactère en dictionnaire
    result2 = ast.literal_eval(result["human_address"])  # idem
    latitude = result["latitude"]
    longitude = result["longitude"]
    address = result2["address"]
    city = result2["city"]
    state = result2["state"]
    zipcode = result2["zip"]
    return latitude, longitude, address, city, state, zipcode

In [11]:
df_2015["Latitude"], df_2015["Longitude"], df_2015["Address"], df_2015["City"], df_2015["State"], df_2015["ZipCode"] = \
    zip(*df_2015["Location"].map(extract_location_features))

La variable déjà présente dans les données `Zip Codes` contient des codes postaux ne correspondant pas à Seattle, contrairement à ceux extraits dans la variable `Location`. Supprimons les variables `Zip Codes` et `Location` :

In [12]:
df_2015[["Zip Codes", "ZipCode"]].head()

Zip Codes ZipCode
0      18081   98101
1      18081   98101
2      18081   98101
3      18081   98101
4      19576   98121

In [13]:
df_2015 = df_2015.drop(["Location", "Zip Codes"], axis=1)

## 2016

In [14]:
df_2016 = data_2016.copy()

In [15]:
get_dataset_overview(df_2016)

####################  DF_2016  ####################

>>> df_2016 contient 3376 lignes et 46 colonnes.

>>> df_2016 contient les variables suivantes :
 ['OSEBuildingID', 'DataYear', 'BuildingType', 'PrimaryPropertyType', 'PropertyName', 'Address', 'City', 'State', 'ZipCode', 'TaxParcelIdentificationNumber', 'CouncilDistrictCode', 'Neighborhood', 'Latitude', 'Longitude', 'YearBuilt', 'NumberofBuildings', 'NumberofFloors', 'PropertyGFATotal', 'PropertyGFAParking', 'PropertyGFABuilding(s)', 'ListOfAllPropertyUseTypes', 'LargestPropertyUseType', 'LargestPropertyUseTypeGFA', 'SecondLargestPropertyUseType', 'SecondLargestPropertyUseTypeGFA', 'ThirdLargestPropertyUseType', 'ThirdLargestPropertyUseTypeGFA', 'YearsENERGYSTARCertified', 'ENERGYSTARScore', 'SiteEUI(kBtu/sf)', 'SiteEUIWN(kBtu/sf)', 'SourceEUI(kBtu/sf)', 'SourceEUIWN(kBtu/sf)', 'SiteEnergyUse(kBtu)', 'SiteEnergyUseWN(kBtu)', 'SteamUse(kBtu)', 'Electricity(kWh)', 'Electricity(kBtu)', 'NaturalGas(therms)', 'NaturalGas(kBtu)', 'Default

Comments  Outlier  YearsENERGYSTARCertified  \
Missing Values       3376.0  3344.00                   3257.00   
% of Total Values     100.0    99.05                     96.48   

                   ThirdLargestPropertyUseTypeGFA  \
Missing Values                            2780.00   
% of Total Values                           82.35   

                   ThirdLargestPropertyUseType  SecondLargestPropertyUseType  \
Missing Values                         2780.00                       1697.00   
% of Total Values                        82.35                         50.27   

                   SecondLargestPropertyUseTypeGFA  ENERGYSTARScore  \
Missing Values                             1697.00           843.00   
% of Total Values                            50.27            24.97   

                   LargestPropertyUseType  LargestPropertyUseTypeGFA  ZipCode  \
Missing Values                      20.00                      20.00    16.00   
% of Total Values                    0.59                       0.59     0.47   

                   SteamUse(kBtu)  TotalGHGEmissions  NaturalGas(kBtu)  \
Missing Values               9.00               9.00              9.00   
% of Total Values            0.27               0.27              0.27   

                   NaturalGas(therms)  Electricity(kBtu)  Electricity(kWh)  \
Missing Values                   9.00               9.00              9.00   
% of Total Values                0.27               0.27              0.27   

                   SourceEUI(kBtu/sf)  SourceEUIWN(kBtu/sf)  \
Missing Values                   9.00                  9.00   
% of Total Values                0.27                  0.27   

                   ListOfAllPropertyUseTypes  GHGEmissionsIntensity  \
Missing Values                          9.00                   9.00   
% of Total Values                       0.27                   0.27   

                   NumberofBuildings  SiteEUI(kBtu/sf)  SiteEnergyUseWN(kBtu)  \
Missing Values                  8.00              7.00                   6.00   
% of Total Values               0.24              0.21                   0.18   

                   SiteEUIWN(kBtu/sf)  SiteEnergyUse(kBtu)  
Missing Values                   6.00                 5.00  
% of Total Values                0.18                 0.15

OSEBuildingID  DataYear    BuildingType          PrimaryPropertyType  \
3133          40067      2016  NonResidential  Small- and Mid-Sized Office   
144             232      2016  NonResidential                        Hotel   
1231          21318      2016  NonResidential  Small- and Mid-Sized Office   

          PropertyName              Address     City State  ZipCode  \
3133     Olympic Block       101 Yesler Way  Seattle    WA  98104.0   
144   Silver Cloud Inn  1150 Fairview Ave N  Seattle    WA  98109.0   
1231    Westlake Place      1520 4th Avenue  Seattle    WA  98101.0   

     TaxParcelIdentificationNumber  CouncilDistrictCode Neighborhood  \
3133                    5247800440                    7     DOWNTOWN   
144                     4088802955                    3   LAKE UNION   
1231                    1975700195                    7     DOWNTOWN   

      Latitude  Longitude  YearBuilt  NumberofBuildings  NumberofFloors  \
3133  47.60148 -122.33379       1985                1.0               6   
144   47.62972 -122.32906       1998                1.0               5   
1231  47.61091 -122.33667       1907                1.0               6   

      PropertyGFATotal  PropertyGFAParking  PropertyGFABuilding(s)  \
3133             73102                   0                   73102   
144             123920               30000                   93920   
1231             35200                   0                   35200   

          ListOfAllPropertyUseTypes LargestPropertyUseType  \
3133                Office, Parking                 Office   
144   Hotel, Parking, Swimming Pool                  Hotel   
1231                         Office                 Office   

      LargestPropertyUseTypeGFA SecondLargestPropertyUseType  \
3133                    92723.0                      Parking   
144                    123920.0                      Parking   
1231                    35200.0                          NaN   

      SecondLargestPropertyUseTypeGFA ThirdLargestPropertyUseType  \
3133                          18364.0                         NaN   
144                           30000.0               Swimming Pool   
1231                              NaN                         NaN   

      ThirdLargestPropertyUseTypeGFA YearsENERGYSTARCertified  \
3133                             NaN                      NaN   
144                              0.0                      NaN   
1231                             NaN                      NaN   

      ENERGYSTARScore  SiteEUI(kBtu/sf)  SiteEUIWN(kBtu/sf)  \
3133             84.0         46.500000           48.400002   
144              79.0         75.599998           78.099998   
1231              8.0         85.199997           85.199997   

      SourceEUI(kBtu/sf)  SourceEUIWN(kBtu/sf)  SiteEnergyUse(kBtu)  \
3133          145.899994            151.800003           4307238.50   
144           148.199997            152.199997           9373179.00   
1231          267.500000            267.500000           2998208.25   

      SiteEnergyUseWN(kBtu)  SteamUse(kBtu)  Electricity(kWh)  \
3133             4483478.00             0.0        1262379.25   
144              9676783.00             0.0        1195550.25   
1231             2998208.25             0.0         878724.50   

      Electricity(kBtu)  NaturalGas(therms)  NaturalGas(kBtu)  DefaultData  \
3133          4307238.0             0.00000               0.0        False   
144           4079217.0         52939.60938         5293961.0        False   
1231          2998208.0             0.00000               0.0        False   

      Comments ComplianceStatus Outlier  TotalGHGEmissions  \
3133       NaN        Compliant     NaN              30.03   
144        NaN        Compliant     NaN             309.60   
1231       NaN        Compliant     NaN              20.90   

      GHGEmissionsIntensity  
3133                   0.41  
144                    2.50  
1231                   0.59

In [16]:
df_2016 = df_2016.loc[:, df_2016.isnull().mean() < .5]

Regardons quelles variables se trouvent uniquement dans `df_2016` : 

In [17]:
set(df_2016.columns) - set(df_2015.columns)

{'GHGEmissionsIntensity', 'TotalGHGEmissions'}

Regardons à présent quelles variables se trouvent uniquement dans `df_2015`:

In [18]:
set(df_2015.columns) - set(df_2016.columns)

{'GHGEmissions(MetricTonsCO2e)',
 'GHGEmissionsIntensity(kgCO2e/ft2)',
 'OtherFuelUse(kBtu)',
 'SPD Beats',
 'Seattle Police Department Micro Community Policing Plan Areas'}

- La variable `GHGEmissionsIntensity` des données de 2016 correspond à la variable `GHGEmissionsIntensity(kgCO2e/ft2)` des données de 2015.
- La variable `TotalGHGEmissions` des données de 2016 correspond à la variable `GHGEmissions(MetricTonsCO2e)` des données de 2015. 
- Nous allons __renommer les variables de 2015 avec les noms de 2016 :__

In [19]:
df_2015.rename(columns={'GHGEmissionsIntensity(kgCO2e/ft2)':'GHGEmissionsIntensity',
                        'GHGEmissions(MetricTonsCO2e)':'TotalGHGEmissions'}, inplace=True)

Nous allons supprimer les variables `OtherFuelUse(kBtu)`, `SPD Beats` et `Seattle Police Dep[...]` des données de 2015.

In [20]:
df_2015.drop(['SPD Beats',
              'OtherFuelUse(kBtu)',
              'Seattle Police Department Micro Community Policing Plan Areas'], inplace=True, axis=1)

In [21]:
print(set(df_2015.columns) - set(df_2016.columns))
print(set(df_2016.columns) - set(df_2015.columns))

set()
set()


Les données de 2015 et de 2016 contiennent maintenant les mêmes variables, nous pouvons les rassembler au sein d'un seul jeu de données `df` : 

In [101]:
df = pd.concat([df_2015, df_2016], axis=0).reset_index(drop=True)

# Analyse exploratoire des données 

## Objectif

- Comprendre du mieux possible nos données.

In [102]:
df.head()

OSEBuildingID  DataYear    BuildingType PrimaryPropertyType  \
0              1      2015  NonResidential               Hotel   
1              2      2015  NonResidential               Hotel   
2              3      2015  NonResidential               Hotel   
3              5      2015  NonResidential               Hotel   
4              8      2015  NonResidential               Hotel   

            PropertyName TaxParcelIdentificationNumber  CouncilDistrictCode  \
0   MAYFLOWER PARK HOTEL                     659000030                    7   
1        PARAMOUNT HOTEL                     659000220                    7   
2           WESTIN HOTEL                     659000475                    7   
3              HOTEL MAX                     659000640                    7   
4  WARWICK SEATTLE HOTEL                     659000970                    7   

  Neighborhood  YearBuilt  NumberofBuildings  NumberofFloors  \
0     DOWNTOWN       1927                1.0            12.0   
1     DOWNTOWN       1996                1.0            11.0   
2     DOWNTOWN       1969                1.0            41.0   
3     DOWNTOWN       1926                1.0            10.0   
4     DOWNTOWN       1980                1.0            18.0   

   PropertyGFATotal  PropertyGFAParking  PropertyGFABuilding(s)  \
0             88434                   0                   88434   
1            103566               15064                   88502   
2            961990                   0                  961990   
3             61320                   0                   61320   
4            119890               12460                  107430   

       ListOfAllPropertyUseTypes LargestPropertyUseType  \
0                          Hotel                  Hotel   
1     Hotel, Parking, Restaurant                  Hotel   
2  Hotel, Parking, Swimming Pool                  Hotel   
3                          Hotel                  Hotel   
4  Hotel, Parking, Swimming Pool                  Hotel   

   LargestPropertyUseTypeGFA  ENERGYSTARScore  SiteEUI(kBtu/sf)  \
0                    88434.0             65.0              78.9   
1                    83880.0             51.0              94.4   
2                   757243.0             18.0              96.6   
3                    61320.0              1.0             460.4   
4                   123445.0             67.0             120.1   

   SiteEUIWN(kBtu/sf)  SourceEUI(kBtu/sf)  SourceEUIWN(kBtu/sf)  \
0                80.3               173.5                 175.1   
1                99.0               191.3                 195.2   
2                99.7               242.7                 246.5   
3               462.5               636.3                 643.2   
4               122.1               228.8                 227.1   

   SiteEnergyUse(kBtu)  SiteEnergyUseWN(kBtu)  SteamUse(kBtu)  \
0            6981428.0              7097539.0       2023032.0   
1            8354235.0              8765788.0             0.0   
2           73130656.0             75506272.0      19660404.0   
3           28229320.0             28363444.0      23458518.0   
4           14829099.0             15078243.0             0.0   

   Electricity(kWh)  Electricity(kBtu)  NaturalGas(therms)  NaturalGas(kBtu)  \
0         1080307.0          3686160.0             12724.0         1272388.0   
1         1144563.0          3905411.0             44490.0         4448985.0   
2        14583930.0         49762435.0             37099.0         3709900.0   
3          811521.0          2769023.0             20019.0         2001894.0   
4         1777841.0          6066245.0             87631.0         8763105.0   

   TotalGHGEmissions  GHGEmissionsIntensity DefaultData ComplianceStatus  \
0             249.43                   2.64          No        Compliant   
1             263.51                   2.38          No        Compliant   
2            2061.48                   1.92         Yes        Compliant   
3     

Supprimons les variables `OSEBuildingID`, `DataYear` :

In [103]:
df.drop(["OSEBuildingID", "DataYear"], inplace=True, axis=1)

In [104]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6716 entries, 0 to 6715
Data columns (total 37 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   BuildingType                   6716 non-null   object 
 1   PrimaryPropertyType            6716 non-null   object 
 2   PropertyName                   6716 non-null   object 
 3   TaxParcelIdentificationNumber  6714 non-null   object 
 4   CouncilDistrictCode            6716 non-null   int64  
 5   Neighborhood                   6716 non-null   object 
 6   YearBuilt                      6716 non-null   int64  
 7   NumberofBuildings              6708 non-null   float64
 8   NumberofFloors                 6708 non-null   float64
 9   PropertyGFATotal               6716 non-null   int64  
 10  PropertyGFAParking             6716 non-null   int64  
 11  PropertyGFABuilding(s)         6716 non-null   int64  
 12  ListOfAllPropertyUseTypes      6580 non-null   o

In [105]:
# Remarque : combinaison linéaire entre ces 3 variables
(df["PropertyGFATotal"] == df["PropertyGFABuilding(s)"] + df["PropertyGFAParking"]).sum() == len(df)

True

## Visualisation des variables cibles

Prenons pour variables cibles :
- `SiteEnergyUse(kBtu)` : correspond à la quantité annuelle d'énergie consommée par la propriété, toutes sources d'énergie confondues.
- `TotalGHGEmissions` : correspond à la quantité totale d'émissions de gaz à effet de serre, y compris le dioxyde de carbone, le méthane et les gaz d'oxyde nitreux rejetés dans l'atmosphère en raison de la consommation d'énergie de la propriété, mesurée en tonnes métriques d'équivalent en dioxyde de carbone.

# SiteEnergyUse(kBtu)

In [106]:
fig = px.ecdf(df, x=["SiteEnergyUse(kBtu)"],
              markers=True,
              lines=False,
              marginal="histogram",
              title="Distribution de la consommation d'énergie")
fig.show()

In [107]:
pd.DataFrame(df["SiteEnergyUse(kBtu)"].describe().apply(lambda x: format(x, "f")))

SiteEnergyUse(kBtu)
count         6701.000000
mean       5194673.270239
std       18136475.382380
min              0.000000
25%         920068.875000
50%        1791071.375000
75%        4135280.250000
max      873923712.000000

In [108]:
fig = px.ecdf(df,
              x=["TotalGHGEmissions"],
              markers=True,
              lines=False,
              marginal="histogram",
              title="Distribution des émissions de gaz à effet de serre")
fig.show()

In [109]:
pd.DataFrame(df["TotalGHGEmissions"].describe().apply(lambda x: format(x, "f")))

TotalGHGEmissions
count       6697.000000
mean         114.935638
std          478.876573
min           -0.800000
25%            9.450000
50%           33.180000
75%           91.530000
max        16870.980000

Voyons à présent la relation entre les __émissions de gaz à effet de serre__ et la __consommation totale d'énergie__ :

In [110]:
fig = px.scatter(df, x="TotalGHGEmissions", y="SiteEnergyUse(kBtu)", trendline="ols")
fig.show()

Les 2 variables semblent positivement corrélées : une forte émission de gaz à effet de serre a tendance à être associée à une forte consommation d'énergie.

In [111]:
# Conversion des variables longitude et latitude en numérique
df[["Longitude", "Latitude"]] = df[["Longitude", "Latitude"]].apply(pd.to_numeric, errors='coerce')

In [112]:
# Suppression des observations où les variables cibles sont manquantes
df = df.dropna(subset=['TotalGHGEmissions'], axis=0)

In [113]:
outliers = df["TotalGHGEmissions"] > 1_500
df_without_outliers = df[~outliers]

In [114]:
get_dataset_shape(df)
get_dataset_shape(df_without_outliers)

>>> df contient 6697 lignes et 37 colonnes.

>>> df_without_outliers contient 6642 lignes et 37 colonnes.



In [115]:
# discretisation de la variable de consommation d'énergie pour la visualisation
df_without_outliers.insert(1, "SiteEnergyUse(kBtu)_range",
                           pd.cut(x=df_without_outliers['SiteEnergyUse(kBtu)'], bins=10, labels=False))

- Taille du cercle = consommation d'énergie
- Couleur du cercle = émission de gaz à effet de serre

In [116]:
fig = px.scatter_mapbox(df_without_outliers,
                        lat="Latitude",
                        lon="Longitude",
                        color="TotalGHGEmissions",
                        size="SiteEnergyUse(kBtu)_range",
                        color_continuous_scale=px.colors.sequential.Redor,
                        size_max=15,
                        zoom=10,
                        mapbox_style = "carto-positron",
                        hover_data = ["CouncilDistrictCode"])
fig.show()

# BuildingType

In [117]:
fig = px.pie(df_without_outliers, "BuildingType")
fig.show()

# PrimaryPropertyType

In [118]:
fig = px.pie(df_without_outliers, "PrimaryPropertyType")
fig.update_traces(textposition='inside')
fig.update_layout(uniformtext_minsize=12, uniformtext_mode='hide')
fig.show()

# PropertyName

In [119]:
corpus = df_without_outliers["PropertyName"]
vectorizer = CountVectorizer(stop_words=english_stops, min_df=100, ngram_range=(1, 2))
bag_of_words = vectorizer.fit_transform(corpus)
bag_of_words = pd.DataFrame(data=bag_of_words.toarray(), columns=vectorizer.get_feature_names())
d = pd.DataFrame(bag_of_words.sum()).reset_index()
d = d.rename(columns={'index':'PropertyName', 0:'Count'}).sort_values('Count', ascending=False)

In [120]:
# pie chart
fig = px.pie(d, values='Count', names='PropertyName')
fig.update_traces(textposition='inside')
fig.update_layout(uniformtext_minsize=12, uniformtext_mode='hide')
fig.show()

In [121]:
# bar chart
fig = px.bar(d, x='PropertyName', y='Count')
fig.show()

# TaxParcelIdentificationNumber

In [123]:
df_without_outliers = df_without_outliers.drop("TaxParcelIdentificationNumber", axis=1)

# CouncilDistrictCode

In [147]:
df_without_outliers["CouncilDistrictCode"].value_counts()

7    2047
3    1156
2    1015
4     702
5     677
1     556
6     489
Name: CouncilDistrictCode, dtype: int64

In [148]:
d = df_without_outliers.groupby("CouncilDistrictCode")[["Longitude", "Latitude"]].mean().reset_index()
d.insert(0, "size", [8] * len(d))
d

size  CouncilDistrictCode   Longitude   Latitude
0     8                    1 -122.372178  47.553733
1     8                    2 -122.316024  47.568666
2     8                    3 -122.316469  47.615214
3     8                    4 -122.313072  47.661768
4     8                    5 -122.324383  47.713888
5     8                    6 -122.364988  47.672793
6     8                    7 -122.348427  47.621408

In [149]:
fig = px.scatter_mapbox(d,
                        lat="Latitude",
                        lon="Longitude",
                        color="CouncilDistrictCode",
                        size="size",
                        #color_continuous_scale=px.colors.sequential.Redor,
                        size_max=15,
                        zoom=10,
                        mapbox_style="carto-positron")
fig.show()

In [122]:
df_without_outliers.columns

Index(['BuildingType', 'SiteEnergyUse(kBtu)_range', 'PrimaryPropertyType',
       'PropertyName', 'TaxParcelIdentificationNumber', 'CouncilDistrictCode',
       'Neighborhood', 'YearBuilt', 'NumberofBuildings', 'NumberofFloors',
       'PropertyGFATotal', 'PropertyGFAParking', 'PropertyGFABuilding(s)',
       'ListOfAllPropertyUseTypes', 'LargestPropertyUseType',
       'LargestPropertyUseTypeGFA', 'ENERGYSTARScore', 'SiteEUI(kBtu/sf)',
       'SiteEUIWN(kBtu/sf)', 'SourceEUI(kBtu/sf)', 'SourceEUIWN(kBtu/sf)',
       'SiteEnergyUse(kBtu)', 'SiteEnergyUseWN(kBtu)', 'SteamUse(kBtu)',
       'Electricity(kWh)', 'Electricity(kBtu)', 'NaturalGas(therms)',
       'NaturalGas(kBtu)', 'TotalGHGEmissions', 'GHGEmissionsIntensity',
       'DefaultData', 'ComplianceStatus', 'Latitude', 'Longitude', 'Address',
       'City', 'State', 'ZipCode'],
      dtype='object')

In [133]:
fig = px.pie(df_without_outliers, "Neighborhood")
fig.update_traces(textposition='inside')
fig.update_layout(uniformtext_minsize=12, uniformtext_mode='hide')
fig.show()

In [150]:
df_without_outliers["Neighborhood"] = df_without_outliers["Neighborhood"].str.lower() 

In [151]:
d = df_without_outliers.groupby("Neighborhood")[["Longitude", "Latitude"]].mean().reset_index()
d.insert(0, "size", [8] * len(d))
d

size            Neighborhood   Longitude   Latitude
0      8                 ballard -122.380774  47.672228
1      8                 central -122.305387  47.608356
2      8                delridge -122.360184  47.540315
3      8  delridge neighborhoods -122.374410  47.540670
4      8                downtown -122.337625  47.608638
5      8                    east -122.320406  47.616961
6      8        greater duwamish -122.323526  47.564709
7      8              lake union -122.337665  47.638013
8      8   magnolia / queen anne -122.362461  47.634282
9      8                   north -122.310051  47.713208
10     8               northeast -122.304643  47.667196
11     8               northwest -122.344701  47.704306
12     8               southeast -122.280708  47.549372
13     8               southwest -122.386311  47.564625

In [152]:
fig = px.scatter_mapbox(d,
                        lat="Latitude",
                        lon="Longitude",
                        color="Neighborhood",
                        size="size",
                        #color_continuous_scale=px.colors.sequential.Redor,
                        size_max=15,
                        zoom=9.5,
                        mapbox_style="carto-positron")
fig.show()

- Rassembler delridge et delride neighborboods
- Si je suis chaud : polygones des districts, voire des quartiers.

In [154]:
fig = px.treemap(df_without_outliers,
                 path=[px.Constant("all"), 'CouncilDistrictCode', 'Neighborhood'])
                 #values='TotalGHGEmissions')
fig.update_traces(root_color="lightgrey")
fig.update_layout(margin = dict(t=50, l=25, r=25, b=25))
fig.show()